In [1]:
from MOFChemicalFormula import MOFChemicalFormula
from ase.io import read as ase_read
from ase.io import write as ase_write

from ase import neighborlist
from ase.formula import Formula
from ase.build import sort
import networkx as nx

import glob
import subprocess
import json

%load_ext autoreload
%autoreload 2


In [2]:
# Set time limit for CIFs read using ASE. Avoid super large CIF

import signal
import time

class Timeout(Exception):
    pass

def handler(sig, frame):
    raise Timeout

In [3]:
def remove_solvent(cif, output_directory, formula, added_identifier='_removed_ions'):
    
    def dict2str(dct):
        """Convert symbol-to-number dict to str.
        """
        return ''.join(symb + (str(n)) for symb, n in dct.items())
    
    try:    
        mof = ase_read(cif)
    except:
        print("Cannot read {} using ASE".format(cif))
        return False, 'Error'
    
    if '/' in cif:
        name = cif.split('/')[-1].split('.')[:-1] # If '/' in path to CIF
    else:
        name = cif.split('.')[:-1] # CIF file name 
    if len(name) == 1:
        output_name = name[0] + added_identifier + '.cif'
    else:
        output_name = '.'.join(name) + added_identifier + '.cif'

    ions_index = []
    final_multiplier = 0 
    final_check = False
    mofchemform = MOFChemicalFormula()

    cutOff = neighborlist.natural_cutoffs(mof)
    neighborList = neighborlist.NeighborList(cutOff, self_interaction=False, bothways=True, skin=0.3)
    neighborList.update(mof)
    G = nx.Graph()

    for k in range(len(mof)):
        tup = (k, {"element":"{}".format(mof.get_chemical_symbols()[k]), "pos": mof.get_positions()[k]})
        G.add_nodes_from([tup])

    for k in range(len(mof)):
        for i in neighborList.get_neighbors(k)[0]:
            G.add_edge(k, i)

    Gcc = sorted(nx.connected_components(G), key=len, reverse=True)

    mof_formula = mof.symbols.formula.count()
    mof_formula = dict2str(mof_formula)
    comp_form = []
    comp_ind = []

    for index, g in enumerate(Gcc):
        g = list(g)
        fragment = mof[g]
        fragment = sort(fragment)
        form_dict = fragment.symbols.formula.count()
        comp_form.append(dict2str(form_dict))
        component_index = []
        for k in Gcc[index]:
            component_index.append(k)
        comp_ind.append(component_index)
    
    csd_dict = mofchemform.element_dict(formula)
    comp_dict = [mofchemform.element_dict(i) for i in comp_form]
    
    for idx, cdict in enumerate(comp_dict):
        check, multiplier = mofchemform.is_multiplier(csd_dict, cdict)
        if check == True:
            print(cdict, csd_dict, multiplier)
            final_check = True
            final_multiplier += multiplier
        else:
            for i in comp_ind[idx]:
                ions_index.append(i)
    if final_check == True:
        if len(ions_index) > 0:
            ions_index = sorted(ions_index, reverse=True)
            del mof[ions_index]
            ase_write('{}/{}'.format(output_directory, output_name), mof)
        else:
            ase_write('{}/{}'.format(output_directory, output_name), mof)
    return final_check, final_multiplier

In [4]:
f = open('data/Anionic_MOFs_formula.json', 'r')
data = json.load(f)
f.close()


In [5]:
cifpath = 'example_cifs/before_solvent_removal'
output_dir = 'example_cifs/after_solvent_removal'

with open('log.txt', 'w') as f:
    for mof in data:
        signal.signal(signal.SIGALRM, handler)  # register interest in SIGALRM events
        signal.alarm(60)  # timeout in 30 seconds
        try:
            print(mof)
            formula = data[mof]['framework'][0]['formula']
            final_check, final_multiplier = remove_solvent(cifpath + '/' + mof + '.Non-disordered_MOF_subset.cif', output_dir, formula)
            if final_check == True:
                f.write('{},{}\n'.format(mof, final_multiplier))
            else:
                f.write('{},FAIL\n'.format(mof))

        except Timeout:
            print('{} took too long'.format(mof))
            continue

ABAYIO


/home/tdpham/.local/lib/python3.8/site-packages/ase/io/cif.py:401: UserWarning: crystal system 'cubic' is not interpreted for space group Spacegroup(225, setting=1). This may result in wrong setting!
  warnings.warn(
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 2 and 11 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 3 and 12 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 4 and 13 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 5 and 14 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spa

/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 2 and 55 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 2 and 56 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 2 and 57 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 2 and 58 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 2 and 59 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarn

{'C': 288, 'Cl': 48, 'H': 96, 'Mn': 48, 'O': 192} {'C': 18, 'H': 6, 'Cl': 3, 'Mn': 3, 'O': 12} 16
ABEDAQ


/home/tdpham/.local/lib/python3.8/site-packages/ase/io/cif.py:401: UserWarning: crystal system 'monoclinic' is not interpreted for space group Spacegroup(14, setting=1). This may result in wrong setting!
  warnings.warn(
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 0 and 189 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 0 and 190 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 1 and 191 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 1 and 192 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages

...

/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 46 and 502 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 79 and 503 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 79 and 504 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 79 and 505 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 81 and 506 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433

ZUZHAF


/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 14 and 216 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 23 and 225 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 39 and 228 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 12 and 237 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 36 and 272 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433

/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 45 and 497 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 45 and 498 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 46 and 500 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 47 and 502 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433: UserWarning: scaled_positions 47 and 503 are equivalent
  warnings.warn('scaled_positions %d and %d '
/home/tdpham/.local/lib/python3.8/site-packages/ase/spacegroup/spacegroup.py:433

ZZZKDE01
{'C': 16, 'H': 24, 'Li': 4, 'O': 28} {'C': 8, 'H': 12, 'Li': 2, 'O': 14} 2
{'C': 16, 'H': 24, 'Li': 4, 'O': 28} {'C': 8, 'H': 12, 'Li': 2, 'O': 14} 2
